# Import libraries

In [34]:
import  pandas as pd
import plotly.graph_objs as go
import plotly.express as pxc
from pyomo.environ import *
import pandapower as pp
import pandapower.networks as pn
import pandas as pd

# Data

## Network Data 

In [35]:
path_save = r'C:\Users\Dell\Documents\GitHub\PINNS_OPF\data\processed'

In [36]:
# Load network characteristics
case5 = pn.case5()

In [37]:
case5

This pandapower network includes the following parameter tables:
   - bus (5 elements)
   - load (3 elements)
   - sgen (1 element)
   - gen (3 elements)
   - ext_grid (1 element)
   - line (6 elements)
   - poly_cost (5 elements)
   - bus_geodata (5 elements)

In [38]:
case5.poly_cost

element        et  cp0_eur  cp1_eur_per_mw  cp2_eur_per_mw2  cq0_eur  \
0        0       gen      0.0            14.0              0.0      0.0   
1        0      sgen      0.0            15.0              0.0      0.0   
2        1       gen      0.0            30.0              0.0      0.0   
3        0  ext_grid      0.0            40.0              0.0      0.0   
4        2       gen      0.0            10.0              0.0      0.0   

   cq1_eur_per_mvar  cq2_eur_per_mvar2  
0               0.0                0.0  
1               0.0                0.0  
2               0.0                0.0  
3               0.0                0.0  
4               0.0                0.0

In [37]:
# Keep only columns name and max min voltages
bus5 = case5.bus[['name','max_vm_pu','min_vm_pu']]
# Define the name of the file
name = r'\bus5.csv'
# Save the file to the path
bus5.to_csv(path_save+name, index=False)

In [12]:
case5.line

name std_type  from_bus  to_bus  length_km  r_ohm_per_km  x_ohm_per_km  \
0  None     None         0       1        1.0       1.48649       14.8649   
1  None     None         0       3        1.0       1.60816       16.0816   
2  None     None         0       4        1.0       0.33856        3.3856   
3  None     None         1       2        1.0       0.57132        5.7132   
4  None     None         2       3        1.0       1.57113       15.7113   
5  None     None         3       4        1.0       1.57113       15.7113   

   c_nf_per_km  g_us_per_km      max_i_ka   df  parallel type  in_service  \
0    35.702054          0.0      1.004087  1.0         1   ol        True   
1    32.994314          0.0  99999.000000  1.0         1   ol        True   
2   156.748063          0.0  99999.000000  1.0         1   ol        True   
3    92.865455          0.0  99999.000000  1.0         1   ol        True   
4    33.796607          0.0  99999.000000  1.0         1   ol        True   
5    33.796607          0.0      0.602452  1.0         1   ol        True   

   max_loading_percent  
0                100.0  
1                100.0  
2                100.0  
3                100.0  
4                100.0  
5                100.0

In [38]:
# Keep only columns we need
line5 = case5.line[['from_bus','to_bus','r_ohm_per_km','x_ohm_per_km','max_i_ka']]
# Define the name of the file
name = r'\line5.csv'
# Save the file to the path
line5.to_csv(path_save+name, index=False)

In [18]:
case5.gen

name  bus    p_mw  vm_pu  sn_mva  min_q_mvar  max_q_mvar  scaling  slack  \
0  None    0   40.00    1.0     NaN       -30.0        30.0      1.0  False   
1  None    2  323.49    1.0     NaN      -390.0       390.0      1.0  False   
2  None    4  466.51    1.0     NaN      -450.0       450.0      1.0  False   

   in_service  slack_weight  type  controllable  max_p_mw  min_p_mw  
0        True           0.0  None          True      40.0       0.0  
1        True           0.0  None          True     520.0       0.0  
2        True           0.0  None          True     600.0       0.0

In [40]:
# Make dataframe for generators
gen = case5.gen[['bus','min_p_mw','max_p_mw','min_q_mvar','max_q_mvar']]
gen['fp_min'] = 0.9
gen['ramp_up'] = 0.5
gen['ramp_down'] = -1
# Define the name of the file
name = r'\asset_gen.csv'
# Save the file to the path
gen.to_csv(path_save+name, index=False)

In [41]:
gen.head()

bus  min_p_mw  max_p_mw  min_q_mvar  max_q_mvar  fp_min  ramp_up  ramp_down
0    0       0.0      40.0       -30.0        30.0     0.9      0.5         -1
1    2       0.0     520.0      -390.0       390.0     0.9      0.5         -1
2    4       0.0     600.0      -450.0       450.0     0.9      0.5         -1

## PV data

In [25]:
pv_data = pd.read_excel(r"C:\Users\Dell\Documents\GitHub\PINNS_OPF\data\raw\PV_data.xlsx")

In [26]:
pv_data.head()
print(pv_data.shape)

(35043, 41)


In [27]:
print(pv_data["Timestamp"][0])
pv_data['Timestamp'] = pd.to_datetime(pv_data['Timestamp'], format='%Y%m%d%H%M%S')
print(pv_data["Timestamp"][0])


20150101001500
2015-01-01 00:15:00


In [28]:
# assuming df is your dataframe and timestamp_col is the name of your timestamp column
pv_data['time_interval'] = pv_data["Timestamp"].diff()

# print the dataframe to verify if time intervals are computed
print(pv_data['time_interval'].value_counts())

0 days 00:15:00      35041
-1 days +23:15:00        1
Name: time_interval, dtype: int64


In [29]:
# assuming df is your dataframe
fig = go.Figure()


# add traces for each column using a loop
for column in pv_data.columns[1:5]:
    fig.add_trace(go.Scatter(x=pv_data['Timestamp'], y=pv_data[column], name=column))

# add layout options
fig.update_layout(title='PV data', xaxis_title='Timestamp', yaxis_title='Value')

# show the plot
fig.show()

In [30]:
# set the timestamp column as the dataframe index
pv_data.set_index('Timestamp', inplace=True)
# resample the dataframe to hourly frequency
pv_data = pv_data.resample('1H').first()

pv_data.head()

No 1 No 2 No 3 No 4 No 5 No 6 No 7 No 8 No 9 No 10 No 11  \
Timestamp                                                                      
2015-01-01 00:00:00    0    0    0    0    0    0    0    0    0     0     0   
2015-01-01 01:00:00    0    0    0    0    0    0    0    0    0     0     0   
2015-01-01 02:00:00    0    0    0    0    0    0    0    0    0     0     0   
2015-01-01 03:00:00    0    0    0    0    0    0    0    0    0     0     0   
2015-01-01 04:00:00    0    0    0    0    0    0    0    0    0     0     0   

                    No 12 No 13 No 14 No 15 No 16 No 17 No 18 No 19 No 20  \
Timestamp                                                                   
2015-01-01 00:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 01:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 02:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 03:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 04:00:00     0     0     0     0     0     0     0     0     0   

                    No 21 No 22 No 23 No 24 No 25 No 26 No 27 No 28 No 29  \
Timestamp                                                                   
2015-01-01 00:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 01:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 02:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 03:00:00     0     0     0     0     0     0     0     0     0   
2015-01-01 04:00:00     0     0     0     0     0     0     0     0     0   

                    No 30 No 31 No 32 No 33 No 34 No 35 No 36 No 37  No 38  \
Timestamp                                                                    
2015-01-01 00:00:00     0     0     0     0     0     0     0     0  0,001   
2015-01-01 01:00:00     0     0     0     0     0     0     0     0      0   
2015-01-01 02:00:00     0     0     0     0     0     0     0     0      0   
2015-01-01 03:00:00     0     0     0     0     0     0     0     0      0   
2015-01-01 04:00:00     0     0     0     0     0     0     0     0      0   

                    No 39 No 40   time_interval  
Timestamp                                        
2015-01-01 00:00:00     0     0 0 days 00:15:00  
2015-01-01 01:00:00     0     0 0 days 00:15:00  
2015-01-01 02:00:00     0     0 0 days 00:15:00  
2015-01-01 03:00:00     0     0 0 days 00:15:00  
2015-01-01 04:00:00     0     0 0 days 00:15:00

In [31]:
# filter the dataframe to keep data for one day only
start_date = '2015-01-02'
end_date = '2015-01-02'
df = pv_data.loc[start_date:end_date].reset_index()

In [32]:
# assuming df is your dataframe
fig = go.Figure()


# add traces for each column using a loop
for column in pv_data.columns[1:5]:
    fig.add_trace(go.Scatter(x=df['Timestamp'], y=df[column], name=column))

# add layout options
fig.update_layout(title='PV data', xaxis_title='Timestamp', yaxis_title='Value')

# show the plot
fig.show()

In [24]:
df.iloc[:,0:3]

Timestamp   No 1   No 2
0  2015-01-02 00:00:00      0      0
1  2015-01-02 01:00:00      0      0
2  2015-01-02 02:00:00      0      0
3  2015-01-02 03:00:00      0      0
4  2015-01-02 04:00:00      0      0
5  2015-01-02 05:00:00      0      0
6  2015-01-02 06:00:00      0      0
7  2015-01-02 07:00:00      0      0
8  2015-01-02 08:00:00      0  0,002
9  2015-01-02 09:00:00   1499  0,838
10 2015-01-02 10:00:00   3189   2289
11 2015-01-02 11:00:00   4058   3143
12 2015-01-02 12:00:00   4,13   3617
13 2015-01-02 13:00:00   4304   3743
14 2015-01-02 14:00:00   4076   3546
15 2015-01-02 15:00:00   3446   3061
16 2015-01-02 16:00:00   1831   1984
17 2015-01-02 17:00:00  0,389  0,038
18 2015-01-02 18:00:00      0      0
19 2015-01-02 19:00:00      0      0
20 2015-01-02 20:00:00      0      0
21 2015-01-02 21:00:00      0      0
22 2015-01-02 22:00:00      0      0
23 2015-01-02 23:00:00      0      0

In [ ]:
build_data = pd.read_csv(r'C:\Users\Dell\Documents\GitHub\PINNS_OPF\data\raw\SCiBER.txt', delimiter='\t')


In [ ]:
print(build_data.head())
print(build_data.shape)
print(build_data.columns)

In [ ]:
build_data= build_data.dropna(axis=1, thresh=len(build_data)-5)

In [ ]:
print(build_data.head())
print(build_data.shape)
print(build_data.columns)

In [ ]:
build_data.isna().sum()

In [ ]:
build_data.median()

In [ ]:
# assuming df is your dataframe
build_data = build_data.fillna(build_data.median())

build_data.isna().sum()

In [ ]:
# assuming df is your dataframe
fig = go.Figure()


# add traces for each column using a loop
for column in build_data.columns[1:10]:
    fig.add_trace(go.Scatter(x=build_data['Timestamp'], y=build_data[column], name=column))

# add layout options
fig.update_layout(title='Building data', xaxis_title='Timestamp', yaxis_title='Wh')

# show the plot
fig.show()

In [ ]:
type(build_data["Timestamp"][0])
# assuming build_data is your dataframe and Timestamp is the name of your timestamp column
build_data['Timestamp'] = pd.to_datetime(build_data['Timestamp'], format='%d.%m.%Y %H:%M')

type(build_data["Timestamp"][0])

In [ ]:
# assuming df is your dataframe and timestamp_col is the name of your timestamp column
build_data['time_interval'] = build_data["Timestamp"].diff()

# print the dataframe to verify if time intervals are computed
print(build_data['time_interval'].value_counts())

In [ ]:
price_data = pd.read_excel(r"C:\Users\Dell\Documents\GitHub\PINNS_OPF\data\raw\20230130_IMBABE_02.xlsx")

In [ ]:
print(price_data.head())
print(price_data.shape)
print(price_data.columns)